In [2]:
files_year = 2004

In [3]:
hijri_months = r"(Muharram|Safar|Rabi[‘’']?\s?al-awwal|Rabi[‘’']?\s?al-thani|Jumada\s?al-awwal|Jumada\s?al-thani|Rajab|Chaâbane|Sha‘ban|Ramadan|Shawwal|Dhou\s?El\s?Kaada|Dhou\s?El\s?Hidja|Dhu\s?al-Qi‘dah|Dhu\s?al-Hijjah)"

In [4]:
import os
import json

In [5]:
data_file_path = f'./files/{str(files_year)}/data.json'

In [6]:
import json
import os

def read_json_file():
    if not os.path.exists(data_file_path):
        return []
    with open(data_file_path, 'r') as f:
        return json.load(f)


all_data = read_json_file()
all_data

[{'pages': 27,
  'content': ['Dimanche 11 Dhou El Kaada 1424\n\nE R 2\n43ème ANNEE DE EUS SN Correspondant au 4 janvier 2004\n\nrappes ISS SP E1\nA C AN D 5N\n\n?ÏÎ\'/’ ‘ J’Ï 5 —0 b\nÔÜW)&L"À@&&}:.ÂALA& &b}hcab‘,&b\\}lÿ\n\nJOURNAIL OFFICIEIL\n\nCONVENTIONS ET ACCORDS INTERNATIONAUX - LOIS ET DECRETS\nARRETES, DECISIONS, AVIS, COMMUNICATIONS ET ANNONCES\n\n(TRADUCTION FRANÇAISE)\n\nDIRECTION ET REDACTION\nSECRETARIAT GENERAL\n\nTunisie\nABONNEMENT Maroc (Pays autres DU GOUVERNEMENT\nque le Maghreb)\nWWW. JORADP. DZ\n\nAbonnement et publicité:\n\nMauritanie\nIMPRIMERIE OFFICIELLE\nLes Vergers, Bir-Mourad Raïs, BP 376\nALGER-GARE\nTél : 021.54.35..06 à 09\nEdition originale..….………...……… 021.65.64.63\ng 1070,00 D.A 2675,00 D.A Fax 0915435 1\n.. … . C.C.P. 3200-50 ALGER\nEdition originale et sa traduction 2140,00 D.A 5350,00 D.A TELEX : 65 180 IMPOF DZ\nBADR: 060.300.0007 68/KG\nETRANGER: (Compte devises)\nBADR: 060.320.0600 12\n\nAlgérie ETRANGER\n\n(Frais d\'expédition en sus)\n\nEdition 

In [7]:
all_data[0]['content']

['Dimanche 11 Dhou El Kaada 1424\n\nE R 2\n43ème ANNEE DE EUS SN Correspondant au 4 janvier 2004\n\nrappes ISS SP E1\nA C AN D 5N\n\n?ÏÎ\'/’ ‘ J’Ï 5 —0 b\nÔÜW)&L"À@&&}:.ÂALA& &b}hcab‘,&b\\}lÿ\n\nJOURNAIL OFFICIEIL\n\nCONVENTIONS ET ACCORDS INTERNATIONAUX - LOIS ET DECRETS\nARRETES, DECISIONS, AVIS, COMMUNICATIONS ET ANNONCES\n\n(TRADUCTION FRANÇAISE)\n\nDIRECTION ET REDACTION\nSECRETARIAT GENERAL\n\nTunisie\nABONNEMENT Maroc (Pays autres DU GOUVERNEMENT\nque le Maghreb)\nWWW. JORADP. DZ\n\nAbonnement et publicité:\n\nMauritanie\nIMPRIMERIE OFFICIELLE\nLes Vergers, Bir-Mourad Raïs, BP 376\nALGER-GARE\nTél : 021.54.35..06 à 09\nEdition originale..….………...……… 021.65.64.63\ng 1070,00 D.A 2675,00 D.A Fax 0915435 1\n.. … . C.C.P. 3200-50 ALGER\nEdition originale et sa traduction 2140,00 D.A 5350,00 D.A TELEX : 65 180 IMPOF DZ\nBADR: 060.300.0007 68/KG\nETRANGER: (Compte devises)\nBADR: 060.320.0600 12\n\nAlgérie ETRANGER\n\n(Frais d\'expédition en sus)\n\nEdition originale, le numéro : 13,50

In [340]:
import json
import pandas as pd
import datefinder

import string

result = []

In [353]:
def extract_data(all_data):
    for content in all_data:

        file = content['content']
        file = file[1: ]

        # get metadata
        metadata = file[1].split('\n')
        
        hijri_date = metadata[0].split('JOURNAL')[0]
        gregorian_date = metadata[1].split('JOURNAL')[0]

        source_match = re.search(r"N°\s*(\d+)", file[1])
        source = source_match.group(1) if source_match else 0

        # start extracting content
        data = {}
        data['metadata'] = {
            "journal_number": source,
            "hijri_date": hijri_date,
            "gregorian_date": gregorian_date
        }
        data['types'] = []

        df = pd.DataFrame(file)

        sommaire = df[0][0].split('\n')
        sommaire = pd.DataFrame(sommaire)
        # print(df)

        titles = [col for col in sommaire[0] if col.isupper()]
        titles = [col for col in titles if not any(char.isdigit() for char in col)]
        titles = [col for col in titles if "OFFICIELLE" or 'JOURNAL' not in col]
        if titles:

            first_title = titles[1]
            titles = titles[1: ]
    
            column_index = [i for i, col in enumerate(sommaire[0]) if col == first_title]
    
            # sommaire = df[: column_index[-1]]
            # sommaire = sommaire[~sommaire.applymap(lambda x: any(char.isdigit() for char in str(x)) or any(char.islower() for char in str(x))).any(axis=1)]
            # sommaire.drop(sommaire[sommaire[0] == ''].index, inplace=True)

            for i, title in enumerate(titles):
                if title != '' and not title.startswith('MINISTERE'):
                    data['types'].append({
                        'type_name': title,
                        'ministries': []
                    })
                elif title != '' and data['types'][-1] and title.startswith('MINISTERE'):
                    data['types'][-1]['ministries'].append({
                        'ministry_name': title,
                        'decrets': []
                    })
            
            for data_type in data['types']: 
                if data_type['ministries'] == []:
                    data_type['ministries'].append({
                        'ministry_name': '',
                        'decrets': []
                    })
            
            df = df[column_index[-1]:]
    
            file = ' '.join(file)

            current_type = None
            decret_pattern = re.compile(r"^(?:Décret exécutif n°\s*\d+.*|Décret présidentiel du\s*\d+.*|Décret présidentiel n°\s*\d+.*|Arrêté du\s*\d+.*|Arrêté interministériel du\s*\d+.*)$", re.IGNORECASE | re.MULTILINE)
            #
            # decret_pattern = re.compile(r"^(?:Décret\s*\d+.*|Arrêté du\s*\d+.*)$", re.IGNORECASE | re.MULTILINE)
            # ^(?:Décret\s?.*|Arrêté du\s*\d+.*)$
            article_pattern = re.compile(r"^(?:Article|Art\.)\s+\d*|l\.", re.IGNORECASE | re.MULTILINE)
            citation_pattern = re.compile(r"^Vu\s+.*$", re.IGNORECASE | re.MULTILINE)
    
            current_decret = ''
            current_articles = []
            current_citations = []
            others = ''
    
            for index, row in df.iterrows():
                content = row[0].strip().split('\n\n')
                for text in content:
                    text = text.replace('\n', ' ')
                    text = text.strip().strip(string.punctuation)
                    if text == '' or 'JOURNAL OFFICIEL DE LA REPUBLIQUE' in text or 'Décrète :' == text or 'Arrête :' == text or 'Sur le rapport' in text or "Le Président de la République" in text or 'x' == text:
                        continue

                    first_index, first_row = next(iter(df.iterrows()))
                    if index == first_index:
                        current_type = data["types"][0]
                    else:
                        for entry in data["types"]:
                            if text == entry["type_name"]:
                                current_type = entry  
                                break
                
                    if current_type and text not in [t["type_name"] for t in data["types"]]:
                        ministry = current_type["ministries"][0] 
                        
                        for min_entry in current_type["ministries"]:
                            if min_entry["ministry_name"] and min_entry["ministry_name"].lower() == text.lower():
                                ministry = min_entry
                                current_decret = ''
                                break
                        
                        if decret_pattern.match(text):
                            if current_decret:
                                for structure in ministry["decrets"]:
                                    if structure["decret_title"] == current_decret:
                                        structure["articles"] = current_articles
                                        structure["citations"] = current_citations
                                        structure["others"] = others
                                        break
                    
                            current_decret = text
                            current_articles = []
                            current_citations = []
                            others = ''
                        
                        elif article_pattern.match(text):
                            words = text.strip().split()
                            if words[0] in ['Article', 'Art.']:
                                number = words[1].replace("er.", "").replace(".", "").replace("—", "").replace("&", "")
                                words = words[2:]
                                words = ' '.join(words)
                            current_articles.append({
                                "article_title": 'Article ' + number,
                                "article_content": words
                            })
                    
                        elif current_articles:
                            current_articles[-1]["article_content"] += " " + text
                    
                        elif citation_pattern.match(text):
                            current_citations.append(text)
                        else:
                            others += text
                
                        if not ministry["decrets"] or not any(dec['decret_title'] == current_decret for dec in ministry["decrets"]):
                            ministry["decrets"].append({
                                'decret_title': current_decret,
                                "articles": current_articles,
                                "citations": current_citations,
                                'others': others
                            })
            result.append(data)


import pandas as pd
import re
result = []

extract_data(all_data[: 1])

print(json.dumps(result, indent=4, ensure_ascii=False))

[
    {
        "metadata": {
            "journal_number": "01",
            "hijri_date": "11 Dhou Fl Kaada 1424",
            "gregorian_date": "4 janvier 2004"
        },
        "types": [
            {
                "type_name": "DECRETS",
                "ministries": [
                    {
                        "ministry_name": "",
                        "decrets": [
                            {
                                "decret_title": "",
                                "articles": [],
                                "citations": [],
                                "others": "11 Dhou El Kaada 1424 4 janvier 2004"
                            },
                            {
                                "decret_title": "Décret présidentiel n° 03-516 du 6 Dhou El Kaada 1424 correspondant au 30 décembre 2003 portant transfert de crédits au sein du budget de l’Etat",
                                "articles": [
                                    {
               

In [155]:
# result

In [156]:
# print(json.dumps(result, indent=4, ensure_ascii=False))

In [295]:
file = all_data[0]['content']
# file

In [296]:
file = file[1: ]

In [297]:
df = pd.DataFrame(file)
df

0
0   11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
1   11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
2   11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
3   11 Dhou Fl Kaada 1424\n4 janvier 2004 JOURNAL ...
4   JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N...
5   11 Dhou Fl Kaada 1424\n4 janvier 2004 JOURNAL ...
6   11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
7   11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
8   JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N...
9   11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
10  11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
11  11 Dhou Fl Kaada 1424\n4 janvier 2004 JOURNAL ...
12  11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
13  11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
14  11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
15  11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
16  11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
17  11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
18  JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N...
19  11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
20  JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N...
21  11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
22  11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
23  11 Dhou Fl Kaada 1424\n4 janvier 2004 JOURNAL ...
24  11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
25  11 Dhou Fl Kaada 1424\n4 janvier 2004 JOURNAL ...

In [298]:
df[0]

0     11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
1     11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
2     11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
3     11 Dhou Fl Kaada 1424\n4 janvier 2004 JOURNAL ...
4     JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N...
5     11 Dhou Fl Kaada 1424\n4 janvier 2004 JOURNAL ...
6     11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
7     11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
8     JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N...
9     11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
10    11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
11    11 Dhou Fl Kaada 1424\n4 janvier 2004 JOURNAL ...
12    11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
13    11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
14    11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
15    11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
16    11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
17    11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJ

In [299]:
# df = df[0][0].split('\n')
# df = pd.DataFrame(df)
# df

In [300]:
df[0]

0     11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
1     11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
2     11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
3     11 Dhou Fl Kaada 1424\n4 janvier 2004 JOURNAL ...
4     JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N...
5     11 Dhou Fl Kaada 1424\n4 janvier 2004 JOURNAL ...
6     11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
7     11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
8     JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N...
9     11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
10    11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
11    11 Dhou Fl Kaada 1424\n4 janvier 2004 JOURNAL ...
12    11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
13    11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
14    11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
15    11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
16    11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
17    11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJ

In [301]:
sommaire = df[0][0].split('\n')
sommaire = pd.DataFrame(sommaire)
sommaire

0
0                               11 Dhou El Kaada 1424
1   JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N...
2                                                    
3                                            SOMMAIRE
4                                             DECRETS
..                                                ...
68                                                   
69  Arrêté du 28 Safar 1424 correspondant au 30 av...
70  national destinées à la mise en valeur dans la...
71                                                   
72                                                   

[73 rows x 1 columns]

In [302]:

titles = [col for col in sommaire[0] if col.isupper()]
titles = [col for col in titles if not any(char.isdigit() for char in col)]
titles = [col for col in titles if "OFFICIELLE" or 'JOURNAL' not in col]
titles

['SOMMAIRE',
 'DECRETS',
 'DECISIONS INDIVIDUELLES',
 'ARRETES, DECISIONS ET AVIS',
 'MINISTERE DE LA DEFENSE NATIONALE',
 'MINISTERE DES AFFAIRES RELIGIEUSES ET DES WAKFS',
 'MINISTERE DE L’AGRICULTURE ET DU DEVELOPPEMENT RURAL']

In [303]:
first_title = titles[1]
first_title


'DECRETS'

In [304]:
column_index = [i for i, col in enumerate(sommaire[0]) if col == first_title]
column_index[-1]

4

In [305]:
df = df[column_index[-1]:]
df

0
4   JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N...
5   11 Dhou Fl Kaada 1424\n4 janvier 2004 JOURNAL ...
6   11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
7   11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
8   JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N...
9   11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
10  11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
11  11 Dhou Fl Kaada 1424\n4 janvier 2004 JOURNAL ...
12  11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
13  11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
14  11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
15  11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
16  11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
17  11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
18  JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N...
19  11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
20  JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N...
21  11 Dhou Fl Kaada 1424\n4 janvier 2004\n\nJOURN...
22  11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
23  11 Dhou Fl Kaada 1424\n4 janvier 2004 JOURNAL ...
24  11 Dhou El Kaada 1424\nJOURNAL OFFICIEL DE LA ...
25  11 Dhou Fl Kaada 1424\n4 janvier 2004 JOURNAL ...

In [308]:
for index , row in df.iterrows():
    # print(row[0])
    print(index)

4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25


In [313]:
def process_page(text):
    # Split into paragraphs using '\n\n'
    paragraphs = text.split("\n\n")
    
    # Replace '\n' (line breaks within paragraphs) with spaces
    paragraphs = [p.replace("\n", " ") for p in paragraphs]
    
    return paragraphs  # Returns a list of cleaned paragraphs

# Iterate through DataFrame and process each page
for index, row in df.iterrows():
    paragraphs = process_page(row[0])
    print(f"Page {row[0]}:")
    for para in paragraphs:
        print(f"- {para}")
    print("\n" + "="*50 + "\n")  # Separator for readability


Page JOURNAL OFFICIEL DE LA REPUBLIQUE ALGERIENNE N° 01

11 Dhou El Kaada 1424
4 janvier 2004

Décret présidentiel n° 03-516 du 6 Dhou El Kaada
1424 correspondant au 30 décembre 2003
portant transfert de crédits au sein du budget de
l’Etat.

Le Président de la République,
Sur le rapport du ministre des finances,

Vu la Constitution, notamment ses articles 77-6° et 125
(alinéa 1er);

Vu la loi n° 84-17 du 7 juillet 1984, modifiée et
complétée, relative aux lois de finances;

Vu la loi n° 02-11 du 20 Chaoual 1423 correspondant
au 24 décembre 2002 portant loi de finances pour 2003;

Vu la loi n° 03-05 du 13 Rabie Ethani 1424
correspondant au 14 juin 2003 portant loi de finances
complémentaire pour 2003;

Vu le décret présidentiel du 14 Joumada Ethania 1424
correspondant au 13 août 2003 portant répartition des
crédits ouverts, au titre du budget de fonctionnement par
la loi de finances complémentaire pour 2003, au budget
des charges communes ;

Vu le décret exécutif n° 03-06 du 6 Dhou El K

4